# Algoritmos de ML para imputar datos

Voy a seguir los pasos de este artículo tal cual
https://www.researchgate.net/publication/342065570_Machine_Learning_for_Univariate_Time_Series_Imputation/link/5ee06165299bf1d20bdebd14/download



In [8]:
!pip install plotly

     |████████████████████████████████| 15.3 MB 1.3 MB/s eta 0:00:01


In [9]:
# Basic imports
import csv
import numpy as np
import pandas as pd
from pandas import Series
import datetime
import time
import os
import math

path = "../data" #Path with raw csv files
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.offline import plot

In [10]:
from sklearn.impute import KNNImputer
files = os.listdir(path)
path_postprocess = path + "_postprocess"
#in the cleaning code we insert the rows that are apparently missing

freqs = {'zone_co2.csv':'1min', 'ele.csv': '15min', 'zone_temp_sp_c.csv':'5min', 'occ.csv':'1min', 'zone_temp_exterior.csv':'1min', 'zone_temp_sp_h.csv':'5min', 'site_weather.csv':'15min', 'wifi.csv': '10min', 'zone_temp_interior.csv':'10min'}
starts = {'ele.csv': '2018/1/1 1:00', 'zone_temp_sp_c.csv':'2018/9/15 10:00', 'occ.csv':'2018-05-22 07:00:00', 'zone_temp_exterior.csv':'2018-01-01 00:00:00', 'zone_temp_sp_h.csv':'2018/9/15 10:00', 'site_weather.csv':'2018-01-01 00:00:00', 'wifi.csv': '2018/5/22 00:00', 'zone_temp_interior.csv':'2018-02-22 00:30:00'}
ends = {'ele.csv': '2021/1/1 0:00', 'zone_temp_sp_c.csv':'2021/1/1 0:00', 'occ.csv':'2019-02-21 10:12:00', 'zone_temp_exterior.csv':'2021-01-01 00:00:00', 'zone_temp_sp_h.csv':'2021/1/1 0:00', 'site_weather.csv':'2021-01-01 00:00:00', 'wifi.csv': '2018/7/11 23:50', 'zone_temp_interior.csv':'2021-01-01 00:00:00'}

In [311]:
# Reinicio para probar
file = 'ele.csv'
df = pd.read_csv(path+'/'+file)
start = starts[file]
end = ends[file]
freq = freqs[file]
path_postprocess = path+"_postprocess/data_definitivo"+'/'+file[:-4]+ "_postprocess.csv"
df['date'] = pd.to_datetime(df['date']) 
df =df[(df.date>=start)&(df.date<=end)]
helper=pd.DataFrame({'date': pd.date_range(start, end, freq=freq)})
df = pd.merge(df, helper, on='date', how='outer').sort_values('date')
df = df[(df.date.dt.month ==11) & (df.date.dt.year==2018)]
df['date'] = pd.to_datetime(df['date']) 
df = df[df['date']!=np.datetime64('NAT')]


var='mels_S'

In [80]:
df

date  mels_S  lig_S     mels_N     hvac_N     hvac_S
29622 2018-11-01 00:00:00   5.350  3.625  11.800000  32.222308  35.176154
29623 2018-11-01 00:15:00   4.925  3.625  10.633333  31.566875  34.648750
29624 2018-11-01 00:30:00   4.500  3.560  10.225000  32.629231  35.106429
29625 2018-11-01 00:45:00   4.075  2.200  10.280000  36.058000  34.586667
29626 2018-11-01 01:00:00   3.650  2.680   8.665000  31.907143  33.232000
...                   ...     ...    ...        ...        ...        ...
31423 2018-11-30 22:45:00   9.152  4.534  19.900000  30.780000  16.277857
31424 2018-11-30 23:00:00   8.614  4.394  16.331667  44.707143  20.284286
31425 2018-11-30 23:15:00   8.076  4.318  16.100000  28.735714   7.570714
31426 2018-11-30 23:30:00   7.538  4.300  17.160000  30.061538   2.700000
31427 2018-11-30 23:45:00   7.000  3.960  16.916000  39.966000   7.371333

[2880 rows x 6 columns]

In [74]:
df.iloc[29622]

IndexError: single positional indexer is out-of-bounds

In [44]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=df.date , y=df[var])
)
fig.show()

Vamos a hacer el experimento con la primera mitad del mes, insertando de manera artificial los valores null, probando el funcionamiento en tres huecos diferentes de 2 días. Después, lo probaremos con todo el dataset.
Este algoritmo parte de una suposición: la longitud del dataframe antes y después es mayor que la longitud del hueco. Por el momento, respetamos esa suposición, y veremos si es necesario realizar modificaciones sobre ella:



## Huecos de 2 días




### Primera prueba- RF



In [485]:
df_bueno = df[df.date.dt.day < 15][['date', 'mels_S']].copy()

In [486]:
df_bueno[df_bueno.isnull().any(axis=1)]

Empty DataFrame
Columns: [date, mels_S]
Index: []

In [487]:
valores_reales = df_bueno.loc[df.date.dt.day.isin([5,6])][['date', 'mels_S']]

In [488]:
df_bueno.loc[df.date.dt.day.isin([5,6]), 'mels_S']=np.nan

In [489]:
df_bueno.loc[df.date.dt.day.isin([5,6])]

date  mels_S
30006 2018-11-05 00:00:00     NaN
30007 2018-11-05 00:15:00     NaN
30008 2018-11-05 00:30:00     NaN
30009 2018-11-05 00:45:00     NaN
30010 2018-11-05 01:00:00     NaN
...                   ...     ...
30193 2018-11-06 22:45:00     NaN
30194 2018-11-06 23:00:00     NaN
30195 2018-11-06 23:15:00     NaN
30196 2018-11-06 23:30:00     NaN
30197 2018-11-06 23:45:00     NaN

[192 rows x 2 columns]

In [490]:
df_bueno.iloc[380:390, 1]

30002    2.50
30003    2.40
30004    2.45
30005    2.50
30006     NaN
30007     NaN
30008     NaN
30009     NaN
30010     NaN
30011     NaN
Name: mels_S, dtype: float64

In [491]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=df_bueno.date , y=df_bueno[var])
)
fig.show()

##### Paso 1: 

Para cada gap T sacamos dos dataframes, uno con los datos de antes y otro con los de después
En nuestro código de limpieza tenemos el índice en el que empieza el gap  (t) y el número de filas que dura

In [492]:
df_bueno.shape

(1344, 2)

In [493]:
start_index = {}
starttime = {}
end_index = {}
endtime = {}
gap = {}
k=0
for j in range(0, len(df_bueno.index)):
    
    if ((pd.isnull(df_bueno.iloc[j,1]) or math.isnan(df_bueno.iloc[j,1]))and not pd.isnull(df_bueno.iloc[j-1,1])):
        print("start", j)
        starttime[k]=df_bueno.iloc[j-1,0] #start time of the gap
        start_index[k]=j
    elif (pd.isnull(df_bueno.iloc[j-1,1]) or math.isnan(df_bueno.iloc[j-1,1])) and pd.isnull(df_bueno.iloc[j,1]) == False:
        endtime[k]=df_bueno.iloc[j,0] #end time of the gap
        end_index[k]=j-1
        k=k+1

start 384


In [494]:
k =0
start=start_index[k]
end = end_index[k]

if k+1 == len(start_index):
    final = len(df_bueno.index)
else:
    final = start_index[k+1]
print("Gap: ", k , " \ndf before[", 1, ':', start, ']\ndf after[', end, ':', final, ']')

Gap:  0  
df before[ 1 : 384 ]
df after[ 575 : 1344 ]


In [495]:
df_bueno.iloc[end+1, 1]

7.588888889

In [496]:
df_antes = df_bueno.iloc[0:start, 1]
df_despues = df_bueno.iloc[end+1:final,1 ].loc[::-1]
df_medio = df_bueno.iloc[start:end+1]

In [497]:
assert df_medio.shape[0]+df_despues.shape[0]+df_antes.shape[0]==df_bueno.shape[0]

In [498]:
df_bueno.iloc[start:end+1, 1]

30006   NaN
30007   NaN
30008   NaN
30009   NaN
30010   NaN
         ..
30193   NaN
30194   NaN
30195   NaN
30196   NaN
30197   NaN
Name: mels_S, Length: 192, dtype: float64

In [499]:
df_antes.shape[0]==start

True

In [500]:
# Creamos los dataframes
a = df_antes.tolist()
b=df_despues.tolist()
T = df_bueno[df_bueno.isnull().any(axis=1)].shape[0]
train_antes =[a[i:i+T] for i in range (0, df_antes.shape[0]-T-1)]
test_antes = [a[i+T+1] for i in range(0, df_antes.shape[0]-T-1)]

train_despues = [b[i:i+T] for i in range (0, (df_despues.shape[0])-T-1)]
test_despues = [b[i+T+1] for i in range (0, (df_despues.shape[0])-T-1)]

In [501]:
from sklearn.ensemble import RandomForestRegressor

rf_antes = RandomForestRegressor()
rf_antes.fit(train_antes, test_antes)

RandomForestRegressor()

In [502]:
rf_despues = RandomForestRegressor()
rf_despues.fit(train_despues, test_despues)

RandomForestRegressor()

In [503]:
a_rf=np.array(a)
b_rf=np.array(b)

In [504]:
for i in range(T):
    at = a_rf[start-T+i:start+i]
    a_rf=np.append(a_rf,rf_antes.predict(at.reshape(1,-1)))

    dp = b_rf[df_despues.shape[0]-T+i:df_despues.shape[0]+i]
    b_rf=np.append(b_rf,rf_despues.predict(dp.reshape(1,-1)))

In [505]:
predictions_antes = a_rf[start:start+T]

In [506]:
predictions_despues = b_rf[df_despues.shape[0]:df_despues.shape[0]+T]

In [507]:
gap=(predictions_antes+predictions_despues[::-1])/2

In [508]:
gap.shape[0]

192

In [509]:
df_medio['pred']=gap

/var/folders/bj/wg2_mprn1fl8bf0h7tq_sh2c0000gn/T/ipykernel_14722/2544091104.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [510]:
df_medio =df_medio.merge(valores_reales, right_on='date', left_on='date')

In [511]:

data = [go.Scatter(x=df_medio.index,
                   y=df_medio[col],
                   name=col) for col in ['pred', 'mels_S_y']]

layout = go.Layout(
    title='Energy use',
    yaxis=dict(title='KW'),
    xaxis=dict(title='Date'), width=800, height=400
)

fig = go.Figure(data=data, layout=layout)
fig.update_layout(legend_orientation="v", 
             xaxis_rangeslider_visible=True, xaxis_rangeslider_thickness=0.1, height=600, width=800 )
fig.show()


### Primera prueba- SVR



In [512]:
from sklearn.svm import SVR
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler

svr_antes = make_pipeline(StandardScaler(), SVR(C=1.0, epsilon=0.2))

svr_antes.fit(train_antes, test_antes)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('svr', SVR(epsilon=0.2))])

In [513]:
svr_despues = make_pipeline(StandardScaler(), SVR(C=1.0, epsilon=0.2))

svr_despues.fit(train_despues, test_despues)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('svr', SVR(epsilon=0.2))])

In [514]:
a_svr=np.array(a)
b_svr=np.array(b)

In [515]:
for i in range(T):
    at = a_svr[start-T+i:start+i]
    a_svr=np.append(a_svr,svr_antes.predict(at.reshape(1,-1)))

    dp = b_svr[df_despues.shape[0]-T+i:df_despues.shape[0]+i]
    b_svr=np.append(b_svr,svr_despues.predict(dp.reshape(1,-1)))

In [516]:
predictions_antes_svr = a_svr[start:start+T]

In [517]:
predictions_despues_svr = b_svr[df_despues.shape[0]:df_despues.shape[0]+T]

In [518]:
gap_2=(predictions_antes_svr+predictions_despues_svr[::-1])/2

In [519]:
df_medio['pred_2']=gap_2

In [520]:

data = [go.Scatter(x=df_medio.index,
                   y=df_medio[col],
                   name=col) for col in ['pred', 'mels_S_y', 'pred_2']]

layout = go.Layout(
    title='Energy use',
    yaxis=dict(title='KW'),
    xaxis=dict(title='Date'), width=800, height=400
)

fig = go.Figure(data=data, layout=layout)
fig.update_layout(legend_orientation="v", 
             xaxis_rangeslider_visible=True, xaxis_rangeslider_thickness=0.1, height=600, width=800 )
fig.show()


### Segunda prueba



In [521]:
df_bueno = df[df.date.dt.day < 15][['date', 'mels_S']].copy()

In [522]:
df_bueno[df_bueno.isnull().any(axis=1)]

Empty DataFrame
Columns: [date, mels_S]
Index: []

In [523]:
valores_reales = df_bueno.loc[df.date.dt.day.isin([9,10])][['date', 'mels_S']]

In [524]:
df_bueno.loc[df.date.dt.day.isin([9,10]), 'mels_S']=np.nan

In [525]:
df_bueno.loc[df.date.dt.day.isin([9,10])]

date  mels_S
30390 2018-11-09 00:00:00     NaN
30391 2018-11-09 00:15:00     NaN
30392 2018-11-09 00:30:00     NaN
30393 2018-11-09 00:45:00     NaN
30394 2018-11-09 01:00:00     NaN
...                   ...     ...
30577 2018-11-10 22:45:00     NaN
30578 2018-11-10 23:00:00     NaN
30579 2018-11-10 23:15:00     NaN
30580 2018-11-10 23:30:00     NaN
30581 2018-11-10 23:45:00     NaN

[192 rows x 2 columns]

In [526]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=df_bueno.date , y=df_bueno[var])
)
fig.show()

#### Paso 1: 

Para cada gap T sacamos dos dataframes, uno con los datos de antes y otro con los de después
En nuestro código de limpieza tenemos el índice en el que empieza el gap  (t) y el número de filas que dura

In [527]:
df_bueno.shape

(1344, 2)

In [528]:
start_index = {}
starttime = {}
end_index = {}
endtime = {}
gap = {}
k=0
for j in range(0, len(df_bueno.index)):
    
    if ((pd.isnull(df_bueno.iloc[j,1]) or math.isnan(df_bueno.iloc[j,1]))and not pd.isnull(df_bueno.iloc[j-1,1])):
        print("start", j)
        starttime[k]=df_bueno.iloc[j-1,0] #start time of the gap
        start_index[k]=j
    elif (pd.isnull(df_bueno.iloc[j-1,1]) or math.isnan(df_bueno.iloc[j-1,1])) and pd.isnull(df_bueno.iloc[j,1]) == False:
        endtime[k]=df_bueno.iloc[j,0] #end time of the gap
        end_index[k]=j-1
        k=k+1

start 768


In [529]:
k =0
start=start_index[k]
end = end_index[k]

if k+1 == len(start_index):
    final = len(df_bueno.index)
else:
    final = start_index[k+1]
print("Gap: ", k , " \ndf before[", 1, ':', start, ']\ndf after[', end, ':', final, ']')

Gap:  0  
df before[ 1 : 768 ]
df after[ 959 : 1344 ]


In [530]:
df_bueno.iloc[end+1, 1]

2.2

In [531]:
df_antes = df_bueno.iloc[0:start, 1]
df_despues = df_bueno.iloc[end+1:final,1 ].loc[::-1]
df_medio = df_bueno.iloc[start:end+1]

In [532]:
assert df_medio.shape[0]+df_despues.shape[0]+df_antes.shape[0]==df_bueno.shape[0]

In [533]:
df_bueno.iloc[start:end+1, 1]

30390   NaN
30391   NaN
30392   NaN
30393   NaN
30394   NaN
         ..
30577   NaN
30578   NaN
30579   NaN
30580   NaN
30581   NaN
Name: mels_S, Length: 192, dtype: float64

In [534]:
df_antes.shape[0]==start

True

##### Paso 2: creamos los dataframes para transformar la serie en multivariable

In [535]:
# Creamos los dataframes
a = df_antes.tolist()
b=df_despues.tolist()
T = df_bueno[df_bueno.isnull().any(axis=1)].shape[0]
train_antes =[a[i:i+T] for i in range (0, df_antes.shape[0]-T-1)]
test_antes = [a[i+T+1] for i in range(0, df_antes.shape[0]-T-1)]

train_despues = [b[i:i+T] for i in range (0, (df_despues.shape[0])-T-1)]
test_despues = [b[i+T+1] for i in range (0, (df_despues.shape[0])-T-1)]

##### Paso 3: entrenamos modelo

In [536]:
from sklearn.ensemble import RandomForestRegressor

rf_antes = RandomForestRegressor()
rf_antes.fit(train_antes, test_antes)

RandomForestRegressor()

In [537]:
rf_despues = RandomForestRegressor()
rf_despues.fit(train_despues, test_despues)

RandomForestRegressor()

In [538]:
a_rf=np.array(a)
b_rf=np.array(b)

In [539]:
for i in range(T):
    at = a_rf[start-T+i:start+i]
    a_rf=np.append(a_rf,rf_antes.predict(at.reshape(1,-1)))

    dp = b_rf[df_despues.shape[0]-T+i:df_despues.shape[0]+i]
    b_rf=np.append(b_rf,rf_despues.predict(dp.reshape(1,-1)))

In [540]:
predictions_antes = a_rf[start:start+T]

In [541]:
predictions_despues = b_rf[df_despues.shape[0]:df_despues.shape[0]+T]

In [542]:
gap=(predictions_antes+predictions_despues[::-1])/2

In [543]:
gap.shape[0]

192

In [544]:
df_medio['pred']=gap

/var/folders/bj/wg2_mprn1fl8bf0h7tq_sh2c0000gn/T/ipykernel_14722/2544091104.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [545]:
df_medio =df_medio.merge(valores_reales, right_on='date', left_on='date')

In [546]:

data = [go.Scatter(x=df_medio.index,
                   y=df_medio[col],
                   name=col) for col in ['pred', 'mels_S_y']]

layout = go.Layout(
    title='Energy use',
    yaxis=dict(title='KW'),
    xaxis=dict(title='Date'), width=800, height=400
)

fig = go.Figure(data=data, layout=layout)
fig.update_layout(legend_orientation="v", 
             xaxis_rangeslider_visible=True, xaxis_rangeslider_thickness=0.1, height=600, width=800 )
fig.show()


### Segunda prueba- SVR



In [547]:
from sklearn.svm import SVR
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler

svr_antes = make_pipeline(StandardScaler(), SVR(C=1.0, epsilon=0.2))

svr_antes.fit(train_antes, test_antes)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('svr', SVR(epsilon=0.2))])

In [548]:
svr_despues = make_pipeline(StandardScaler(), SVR(C=1.0, epsilon=0.2))

svr_despues.fit(train_despues, test_despues)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('svr', SVR(epsilon=0.2))])

In [549]:
a_svr=np.array(a)
b_svr=np.array(b)

In [550]:
for i in range(T):
    at = a_svr[start-T+i:start+i]
    a_svr=np.append(a_svr,svr_antes.predict(at.reshape(1,-1)))

    dp = b_svr[df_despues.shape[0]-T+i:df_despues.shape[0]+i]
    b_svr=np.append(b_svr,svr_despues.predict(dp.reshape(1,-1)))

In [551]:
predictions_antes_svr = a_svr[start:start+T]

In [552]:
predictions_despues_svr = b_svr[df_despues.shape[0]:df_despues.shape[0]+T]

In [553]:
gap_2=(predictions_antes_svr+predictions_despues_svr[::-1])/2

In [554]:
df_medio['pred_2']=gap_2

In [555]:

data = [go.Scatter(x=df_medio.index,
                   y=df_medio[col],
                   name=col) for col in ['pred', 'mels_S_y', 'pred_2']]

layout = go.Layout(
    title='Energy use',
    yaxis=dict(title='KW'),
    xaxis=dict(title='Date'), width=800, height=400
)

fig = go.Figure(data=data, layout=layout)
fig.update_layout(legend_orientation="v", 
             xaxis_rangeslider_visible=True, xaxis_rangeslider_thickness=0.1, height=600, width=800 )
fig.show()


## Hyperparemeter tuning en los modelos intermedios

### Repetimos la primera prueba, tuneando el modelo

In [556]:
df_bueno = df[df.date.dt.day < 15][['date', 'mels_S']].copy()

In [557]:
valores_reales = df_bueno.loc[df.date.dt.day.isin([5,6])][['date', 'mels_S']]

In [558]:
df_bueno.loc[df.date.dt.day.isin([5,6]), 'mels_S']=np.nan

In [559]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=df_bueno.date , y=df_bueno[var])
)
fig.show()

##### Paso 1: 

Para cada gap T sacamos dos dataframes, uno con los datos de antes y otro con los de después
En nuestro código de limpieza tenemos el índice en el que empieza el gap  (t) y el número de filas que dura

In [560]:
start_index = {}
starttime = {}
end_index = {}
endtime = {}
gap = {}
k=0
for j in range(0, len(df_bueno.index)):
    
    if ((pd.isnull(df_bueno.iloc[j,1]) or math.isnan(df_bueno.iloc[j,1]))and not pd.isnull(df_bueno.iloc[j-1,1])):
        print("start", j)
        starttime[k]=df_bueno.iloc[j-1,0] #start time of the gap
        start_index[k]=j
    elif (pd.isnull(df_bueno.iloc[j-1,1]) or math.isnan(df_bueno.iloc[j-1,1])) and pd.isnull(df_bueno.iloc[j,1]) == False:
        endtime[k]=df_bueno.iloc[j,0] #end time of the gap
        end_index[k]=j-1
        k=k+1

start 384


In [561]:
k =0
start=start_index[k]
end = end_index[k]

if k+1 == len(start_index):
    final = len(df_bueno.index)
else:
    final = start_index[k+1]
print("Gap: ", k , " \ndf before[", 1, ':', start, ']\ndf after[', end, ':', final, ']')

Gap:  0  
df before[ 1 : 384 ]
df after[ 575 : 1344 ]


In [562]:
df_antes = df_bueno.iloc[0:start, 1]
df_despues = df_bueno.iloc[end+1:final,1 ].loc[::-1]
df_medio = df_bueno.iloc[start:end+1]

In [563]:
assert df_medio.shape[0]+df_despues.shape[0]+df_antes.shape[0]==df_bueno.shape[0]

In [564]:
# Creamos los dataframes
a = df_antes.tolist()
b=df_despues.tolist()
T = df_bueno[df_bueno.isnull().any(axis=1)].shape[0]
train_antes =[a[i:i+T] for i in range (0, df_antes.shape[0]-T-1)]
test_antes = [a[i+T+1] for i in range(0, df_antes.shape[0]-T-1)]

train_despues = [b[i:i+T] for i in range (0, (df_despues.shape[0])-T-1)]
test_despues = [b[i+T+1] for i in range (0, (df_despues.shape[0])-T-1)]

In [567]:
from sklearn.model_selection import RandomizedSearchCV
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4]
# Method of selecting samples for training each tree
bootstrap = [True, False]
# Create the random grid


random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}

In [568]:
from sklearn.ensemble import RandomForestRegressor

rf_antes = RandomForestRegressor()
rf_random_antes = RandomizedSearchCV(estimator = rf_antes, param_distributions = random_grid, n_iter = 100, cv = 3, verbose=2, random_state=42, n_jobs = -1)
rf_random_antes.fit(train_antes, test_antes)

Fitting 3 folds for each of 100 candidates, totalling 300 fits
[CV] END bootstrap=True, max_depth=30, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=400; total time=   0.4s
[CV] END bootstrap=True, max_depth=30, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=400; total time=   0.5s
[CV] END bootstrap=True, max_depth=30, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=400; total time=   0.5s
[CV] END bootstrap=False, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1200; total time=   1.2s
[CV] END bootstrap=False, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1200; total time=   1.4s
[CV] END bootstrap=False, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1200; total time=   1.2s
[CV] END bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=200

RandomizedSearchCV(cv=3, estimator=RandomForestRegressor(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4],
                                        'min_samples_split': [2, 5, 10],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=42, verbose=2)

In [569]:
rf_despues = RandomForestRegressor()
rf_random_despues = RandomizedSearchCV(estimator = rf_despues, param_distributions = random_grid, n_iter = 100, cv = 3, verbose=2, random_state=42, n_jobs = -1)
rf_random_despues.fit(train_despues, test_despues)

Fitting 3 folds for each of 100 candidates, totalling 300 fits
[CV] END bootstrap=True, max_depth=30, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=400; total time=   0.9s
[CV] END bootstrap=True, max_depth=30, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=400; total time=   1.0s
[CV] END bootstrap=True, max_depth=30, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=400; total time=   1.0s
[CV] END bootstrap=False, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1200; total time=   3.1s
[CV] END bootstrap=False, max_depth=10, max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=1200; total time=   3.3s
[CV] END bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=2000; total time=   3.9s
[CV] END bootstrap=True, max_depth=10, max_features=sqrt, min_samples_leaf=1, min_samples_split=5, n_estimators=2000

RandomizedSearchCV(cv=3, estimator=RandomForestRegressor(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4],
                                        'min_samples_split': [2, 5, 10],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=42, verbose=2)

In [580]:
rf_random_antes.best_estimator_

RandomForestRegressor(max_depth=60, max_features='sqrt', min_samples_leaf=2,
                      min_samples_split=10, n_estimators=600)

In [581]:
rf_random_despues.best_estimator_

RandomForestRegressor(max_depth=100, n_estimators=1400)

In [570]:
a_rf=np.array(a)
b_rf=np.array(b)

In [572]:
for i in range(T):
    at = a_rf[start-T+i:start+i]
    a_rf=np.append(a_rf,rf_random_antes.predict(at.reshape(1,-1)))

    dp = b_rf[df_despues.shape[0]-T+i:df_despues.shape[0]+i]
    b_rf=np.append(b_rf,rf_random_despues.predict(dp.reshape(1,-1)))

In [573]:
predictions_antes = a_rf[start:start+T]

In [574]:
predictions_despues = b_rf[df_despues.shape[0]:df_despues.shape[0]+T]

In [575]:
gap=(predictions_antes+predictions_despues[::-1])/2

In [576]:
gap.shape[0]

192

In [577]:
df_medio['pred']=gap

/var/folders/bj/wg2_mprn1fl8bf0h7tq_sh2c0000gn/T/ipykernel_14722/2544091104.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [578]:
df_medio =df_medio.merge(valores_reales, right_on='date', left_on='date')

In [579]:

data = [go.Scatter(x=df_medio.index,
                   y=df_medio[col],
                   name=col) for col in ['pred', 'mels_S_y']]

layout = go.Layout(
    title='Energy use',
    yaxis=dict(title='KW'),
    xaxis=dict(title='Date'), width=800, height=400
)

fig = go.Figure(data=data, layout=layout)
fig.update_layout(legend_orientation="v", 
             xaxis_rangeslider_visible=True, xaxis_rangeslider_thickness=0.1, height=600, width=800 )
fig.show()


Tal y como vemos, no cambia mucho la cosa, por lo que de momento nos quedaremos con los parámetros fijos:

-n_estimators:800
-max_depth = 100


## Hueco más grande en la serie temporal completa

In [582]:
# Reinicio para probar
file = 'ele.csv'
df = pd.read_csv(path+'/'+file)
start = starts[file]
end = ends[file]
freq = freqs[file]
path_postprocess = path+"_postprocess/data_definitivo"+'/'+file[:-4]+ "_postprocess.csv"
df['date'] = pd.to_datetime(df['date']) 
df =df[(df.date>=start)&(df.date<=end)]
helper=pd.DataFrame({'date': pd.date_range(start, end, freq=freq)})
df = pd.merge(df, helper, on='date', how='outer').sort_values('date')
df = df[df['date']!=np.datetime64('NAT')]


var='mels_S'

In [584]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=df.date , y=df[var])
)
fig.update_layout(legend_orientation="v", 
             xaxis_rangeslider_visible=True, xaxis_rangeslider_thickness=0.1, height=600, width=1000 )
fig.show()

In [593]:
# Parece que de febrero a Junio del 2019 no tenemos fallos
df_recortada=df[(df.date>='2019-02-01')&(df.date<='2019-07-16')]
df_recortada[df_recortada.isnull().any(axis=1)]

Empty DataFrame
Columns: [date, mels_S, lig_S, mels_N, hvac_N, hvac_S]
Index: []

Vamos a crear un hueco falso de 10 días, del 20 al 30 de abril. Para ello, procedemos exactamente igual que con los ejemplos anteriores:

In [600]:
df_bueno = df_recortada[['date','mels_S']].copy()

In [601]:
df_bueno[df_bueno.isnull().any(axis=1)]

Empty DataFrame
Columns: [date, mels_S]
Index: []

In [602]:
valores_reales = df_bueno.loc[(df_bueno.date>='2019-04-10')&(df_bueno.date<='2019-04-20')][['date', 'mels_S']]

In [603]:
df_bueno.loc[(df_bueno.date>='2019-04-10')&(df_bueno.date<='2019-04-20'), 'mels_S']=np.nan

In [604]:
df_bueno.loc[(df_bueno.date>='2019-04-10')&(df_bueno.date<='2019-04-20')]

date  mels_S
43607 2019-04-10 00:00:00     NaN
43608 2019-04-10 00:15:00     NaN
43609 2019-04-10 00:30:00     NaN
43610 2019-04-10 00:45:00     NaN
43611 2019-04-10 01:00:00     NaN
...                   ...     ...
44563 2019-04-19 23:00:00     NaN
44564 2019-04-19 23:15:00     NaN
44565 2019-04-19 23:30:00     NaN
44566 2019-04-19 23:45:00     NaN
44567 2019-04-20 00:00:00     NaN

[961 rows x 2 columns]

In [605]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=df_bueno.date , y=df_bueno[var])
)
fig.show()

#### Paso 1: 

Para cada gap T sacamos dos dataframes, uno con los datos de antes y otro con los de después
En nuestro código de limpieza tenemos el índice en el que empieza el gap  (t) y el número de filas que dura

In [606]:
df_bueno.shape

(15841, 2)

In [607]:
start_index = {}
starttime = {}
end_index = {}
endtime = {}
gap = {}
k=0
for j in range(0, len(df_bueno.index)):
    
    if ((pd.isnull(df_bueno.iloc[j,1]) or math.isnan(df_bueno.iloc[j,1]))and not pd.isnull(df_bueno.iloc[j-1,1])):
        print("start", j)
        starttime[k]=df_bueno.iloc[j-1,0] #start time of the gap
        start_index[k]=j
    elif (pd.isnull(df_bueno.iloc[j-1,1]) or math.isnan(df_bueno.iloc[j-1,1])) and pd.isnull(df_bueno.iloc[j,1]) == False:
        endtime[k]=df_bueno.iloc[j,0] #end time of the gap
        end_index[k]=j-1
        k=k+1

start 6528


In [608]:
k =0
start=start_index[k]
end = end_index[k]

if k+1 == len(start_index):
    final = len(df_bueno.index)
else:
    final = start_index[k+1]
print("Gap: ", k , " \ndf before[", 1, ':', start, ']\ndf after[', end, ':', final, ']')

Gap:  0  
df before[ 1 : 6528 ]
df after[ 7488 : 15841 ]


In [609]:
df_bueno.iloc[end+1, 1]

3.5

In [610]:
df_antes = df_bueno.iloc[0:start, 1]
df_despues = df_bueno.iloc[end+1:final,1 ].loc[::-1]
df_medio = df_bueno.iloc[start:end+1]

In [611]:
assert df_medio.shape[0]+df_despues.shape[0]+df_antes.shape[0]==df_bueno.shape[0]

In [623]:
df_antes.shape[0]

6528

In [624]:
df_despues.shape[0]

8352

In [625]:
df_medio.shape[0]

961

In [613]:
df_antes.shape[0]==start

True

##### Paso 2: creamos los dataframes para transformar la serie en multivariable

In [614]:
# Creamos los dataframes
a = df_antes.tolist()
b=df_despues.tolist()
T = df_bueno[df_bueno.isnull().any(axis=1)].shape[0]
train_antes =[a[i:i+T] for i in range (0, df_antes.shape[0]-T-1)]
test_antes = [a[i+T+1] for i in range(0, df_antes.shape[0]-T-1)]

train_despues = [b[i:i+T] for i in range (0, (df_despues.shape[0])-T-1)]
test_despues = [b[i+T+1] for i in range (0, (df_despues.shape[0])-T-1)]

##### Paso 3: entrenamos modelo

In [621]:
len(train_antes)

5566

In [626]:
from sklearn.ensemble import RandomForestRegressor

rf_antes = RandomForestRegressor()
rf_antes.fit(train_antes, test_antes)

RandomForestRegressor()

In [627]:
rf_despues = RandomForestRegressor()
rf_despues.fit(train_despues, test_despues)

RandomForestRegressor()

In [628]:
a_rf=np.array(a)
b_rf=np.array(b)

In [629]:
for i in range(T):
    at = a_rf[start-T+i:start+i]
    a_rf=np.append(a_rf,rf_antes.predict(at.reshape(1,-1)))

    dp = b_rf[df_despues.shape[0]-T+i:df_despues.shape[0]+i]
    b_rf=np.append(b_rf,rf_despues.predict(dp.reshape(1,-1)))

In [630]:
predictions_antes = a_rf[start:start+T]

In [631]:
predictions_despues = b_rf[df_despues.shape[0]:df_despues.shape[0]+T]

In [632]:
gap=(predictions_antes+predictions_despues[::-1])/2

In [633]:
gap.shape[0]

961

In [634]:
df_medio['pred']=gap

/var/folders/bj/wg2_mprn1fl8bf0h7tq_sh2c0000gn/T/ipykernel_14722/2544091104.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [635]:
df_medio =df_medio.merge(valores_reales, right_on='date', left_on='date')

In [636]:

data = [go.Scatter(x=df_medio.index,
                   y=df_medio[col],
                   name=col) for col in ['pred', 'mels_S_y']]

layout = go.Layout(
    title='Energy use',
    yaxis=dict(title='KW'),
    xaxis=dict(title='Date'), width=800, height=400
)

fig = go.Figure(data=data, layout=layout)
fig.update_layout(legend_orientation="v", 
             xaxis_rangeslider_visible=True, xaxis_rangeslider_thickness=0.1, height=600, width=800 )
fig.show()


### Segunda prueba- SVR



In [637]:
from sklearn.svm import SVR
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler

svr_antes = make_pipeline(StandardScaler(), SVR(C=1.0, epsilon=0.2))

svr_antes.fit(train_antes, test_antes)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('svr', SVR(epsilon=0.2))])

In [638]:
svr_despues = make_pipeline(StandardScaler(), SVR(C=1.0, epsilon=0.2))

svr_despues.fit(train_despues, test_despues)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('svr', SVR(epsilon=0.2))])

In [639]:
a_svr=np.array(a)
b_svr=np.array(b)

In [640]:
for i in range(T):
    at = a_svr[start-T+i:start+i]
    a_svr=np.append(a_svr,svr_antes.predict(at.reshape(1,-1)))

    dp = b_svr[df_despues.shape[0]-T+i:df_despues.shape[0]+i]
    b_svr=np.append(b_svr,svr_despues.predict(dp.reshape(1,-1)))

In [641]:
predictions_antes_svr = a_svr[start:start+T]

In [642]:
predictions_despues_svr = b_svr[df_despues.shape[0]:df_despues.shape[0]+T]

In [643]:
gap_2=(predictions_antes_svr+predictions_despues_svr[::-1])/2

In [644]:
df_medio['pred_2']=gap_2

In [645]:

data = [go.Scatter(x=df_medio.index,
                   y=df_medio[col],
                   name=col) for col in ['pred', 'mels_S_y', 'pred_2']]

layout = go.Layout(
    title='Energy use',
    yaxis=dict(title='KW'),
    xaxis=dict(title='Date'), width=800, height=400
)

fig = go.Figure(data=data, layout=layout)
fig.update_layout(legend_orientation="v", 
             xaxis_rangeslider_visible=True, xaxis_rangeslider_thickness=0.1, height=600, width=800 )
fig.show()
